In [3]:
import pandas  as pd 
from itertools import product
from collections import defaultdict
from itertools import groupby
from copy import deepcopy

Estado actual: 
* Pandas es muy lento para lo que quiero hacer
* Trabajo actual: separar los desempates en: Primero wins, despues rounds, despues mapas (probablemente no se implemente)
* Potenciales soluciones: Cambiar la manera de armar la tabla a Numpy (deberia ser lo mas rapido por mucho) Ventajas: velocidad y puedo evaluar por filas los resultados 

-------------------------------------------------------------------------

Arranco casi de 0, problemas con la unicacion de memoria de los objetos y se armo un re quilombo. 
Intento 2 diseño enfocado tabla final que tengo y estructurar desde ese punto hacia atras. 




In [2]:
#Esto es raro, siento que estoy dando vueltas en circulo con este diccionario creando los objetos y volviendo a usarlos 
#Lo termino usando con un zip, lo que puede ser peligroso con el orden y las keys
#Agregar h2h ganados aca, voy a tener que modificar como funcionan las fuciones 
teamNameScores = {
                "name": ["Kru","Lev","100T","mibr","NRG","EG","FUR","LOUD", "2G","G2","C9","SEN"],
                "wins": [6,9,5,1,4,4,3,4,7,00,6,6],
                "loss":[4,1,5,9,6,6,7,6,3,00,4,4],
                "matchWins" : [15,19,12,3,10,10,8,11,15,00,13,13],
                "matchLoss" : [10,4,11,18,13,15,15,14,8,00,13,8],
                "roundWin":[287,296,255,168,238,241,195,249,249,00,270,249],
                "roundLoss":[247,204,232,257,237,281,270,275,214,00,276,214],
                'h2h' : [['FUR','mibr','EG','LOUD','C9','SEN'],
                         ['SEN','NRG','G2','100T','EG','LOUD','FUR'],
                         ['EG','G2','NRG'],
                         ['EG'],
                         ['Kru','LOUD','FUR','mibr'],
                         ['SEN','LOUD'],
                         ['100T','mibr'],
                         ['SEN','G2','mibr','100T'],
                         ['FUR','EG','mibr','Kru','NRG','Kru','SEN'],
                         [], 
                         ['Lev','EG','LOUD','FUR','mibr','NRG'],
                         ['100T','mibr','FUR','NRG']
                         ]
                  }

roundMatches = {
                "week11" : [["Kru","Lev"], ["100T","mibr"],["NRG","EG"], ["FUR","LOUD"],["2G","G2"],["C9","SEN"]],
                "week12" : [["Kru","100T"], ["Lev","mibr"],["NRG","FUR"], ["EG","LOUD"],["C9","G2"],["2G","SEN"]]
                }

In [3]:
teamNameScores = {
    "name": [
        "Kru",
        "Lev",
        "100T",
        "mibr",
        "NRG",
        "EG",
        "FUR",
        "LOUD",
        "2G",
        "GAMERS2",
        "C9",
        "SEN",
    ],
    "wins": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "loss": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "matchWins": [0, 0, 0,0, 0, 0,0, 0, 0, 0, 0, 0],
    "matchLoss": [0,0, 0, 0, 0, 0, 0, 0,0, 0, 0, 0],
    "roundWin": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
    "roundLoss": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
}

roundMatches = {
    "week11": [
        ["Kru", "Lev"],
        ["100T", "mibr"],
        ["NRG", "EG"],
        ["FUR", "LOUD"],
        ["2G", "GAMERS2"],
        ["C9", "SEN"],
    ],
    "week12": [
        ["Kru", "100T"],
        ["Lev", "mibr"],
        ["NRG", "FUR"],
        ["EG", "LOUD"],
        ["C9", "GAMERS2"],
        ["2G", "SEN"],
    ],
}

In [5]:
#Not using this one 
def run_round(matches, teams, previous_results=None) -> list:
    if previous_results is None: #Esto se queda por ser solo 1 UP 
        previous_results = []
        for i, team in enumerate(teams["name"]):
            temp_dict = {
                "UP": 1,
                "Team": team,
                "wins": teams["wins"][i],
                "matchWins": teams["matchWins"][i],
                "matchLoss": teams["matchLoss"][i],
            }
            previous_results.append(temp_dict)

    match_outcomes = list(product([0, 1, 2, 3], repeat=len(matches)))
    new_results = []

    result_mapping = {
        0: (0, 2),  # pierde 0-2
        1: (1, 2),  # pierde 1-2
        2: (2, 1),  # gana 2-1
        3: (2, 0),  # gana 2-0
    }

    test_group = defaultdict(list)
    for result in previous_results:
        test_group[result["UP"]].append(result)

    for up, group in test_group.items():
        simul_teams = {
            team_data["Team"]: {
                "wins": team_data["wins"],
                "matchWins": team_data["matchWins"],
                "matchLoss": team_data["matchLoss"],
            }
            for team_data in group}

        for combination_index, combination in enumerate(match_outcomes, start=1):

            temp_teams = {team: data.copy() for team, data in simul_teams.items()}

            for match_index, result in enumerate(combination):
                team1, team2 = matches[match_index]
                team1_score, team2_score = result_mapping[result]

                if result in [2, 3]:
                    temp_teams[team1]["wins"] += 1
                    temp_teams[team1]["matchWins"] += team1_score
                    temp_teams[team1]["matchLoss"] += team2_score
                    temp_teams[team2]["matchWins"] += team2_score
                    temp_teams[team2]["matchLoss"] += team1_score

                else:
                    temp_teams[team2]["wins"] += 1
                    temp_teams[team2]["matchWins"] += team2_score
                    temp_teams[team2]["matchLoss"] += team1_score
                    temp_teams[team1]["matchWins"] += team1_score
                    temp_teams[team1]["matchLoss"] += team2_score

            new_up = f"{up}-{combination_index}"

            for team, data in temp_teams.items():
                new_results.append(
                    {
                        "UP": new_up,
                        "Team": team,
                        "wins": data["wins"],
                        "matchWins": data["matchWins"],
                        "matchLoss": data["matchLoss"],
                    }
                )

    return new_results

In [9]:
def run_round_delta(matches, teams, previous_results=None) -> list:
    if previous_results is None: #Esto se queda por ser solo 1 UP 
        previous_results = []
        for i, team in enumerate(teams["name"]):
            temp_dict = {
                "UP": 1,
                "Team": team,
                "wins": teams["wins"][i],
                "matchDelta": teams["matchWins"][i] - teams["matchLoss"][i],
                "h2h": teams['h2h'][i]              
            }
            previous_results.append(temp_dict)

    match_outcomes = list(product([0, 1, 2, 3], repeat=len(matches)))
    new_results = []

    result_mapping = {
        0: (0, 2),  # pierde 0-2
        1: (1, 2),  # pierde 1-2
        2: (2, 1),  # gana 2-1
        3: (2, 0),  # gana 2-0
    }

    test_group = defaultdict(list)
    for result in previous_results:
        test_group[result["UP"]].append(result)

    for up, group in test_group.items():
        simul_teams = {
            team_data["Team"]: {
                "wins": team_data["wins"],
                "matchDelta": team_data["matchDelta"],
                'h2h': team_data['h2h']
            }
            for team_data in group}

        for combination_index, combination in enumerate(match_outcomes, start=1):
            temp_teams = deepcopy(simul_teams)            

            for match_index, result in enumerate(combination):
                team1, team2 = matches[match_index]
                team1_score, team2_score = result_mapping[result]
                delta_score = abs(team1_score-team2_score)

                if result in [2, 3]:
                    temp_teams[team1]["wins"] += 1
                    temp_teams[team1]["matchDelta"] += delta_score
                    temp_teams[team2]["matchDelta"] -= delta_score
                    temp_teams[team1]["h2h"] += [team2]

                else:
                    temp_teams[team2]["wins"] += 1
                    temp_teams[team2]["matchDelta"] += delta_score  
                    temp_teams[team1]["matchDelta"] -= delta_score
                    temp_teams[team2]["h2h"] += [team1]

            new_up = f"{up}-{combination_index}"

            for team, data in temp_teams.items():
                new_results.append(
                    {
                        "UP": new_up,
                        "Team": team,
                        "wins": data["wins"],
                        "matchDelta": data["matchDelta"],
                        'h2h': data['h2h']

                    }
                )

    return new_results

In [16]:
def groupby_UP(matchresults):
    group_result = defaultdict(list)
    for result in matchresults:
        group_result[result["UP"]].append(result)
    return group_result

def group_table(teamDict) -> list:
    return  [
    list(group) for _, group in groupby(teamDict, key=lambda x: x[1]["wins"])
    ]

def heriarchy_dict_for_sort(groupby_up_dict: dict) -> dict:
    hierarchy_dict_to_return = {}
    for key in groupby_up_dict.keys():
        hierarchy_dict_to_append = {}
        for team in groupby_up_dict[key]:
            hierarchy_dict_to_append[team["Team"]] = {
                "wins": team["wins"],
                "matchDelta": team["matchDelta"],
                'h2h': team['h2h']
            }
        hierarchy_dict_to_return[key] = hierarchy_dict_to_append
    return hierarchy_dict_to_return

def sort_dict_by_wins(single_up_round) -> list:
    count = 1
    sorted_table = sorted(single_up_round.items(), key =lambda x: (x[1]["wins"], x[1]["matchDelta"]), reverse=True)
    
    grouped_table = group_table(sorted_table)
    
    count += 1
    return grouped_table
#Aca tengo que agregar el desempate y los resultados y no crear todo la lista larga? 

#Tiebreak Rules

def two_teams_tie(tie_teams: list) -> list: #Esta es rara, falla en tablas incompletas (pueden no haber jugado los dos equipos, pero no deberia falla en la ultima ronda)
    if len(tie_teams) != 2:
        print("not 2 tie teams")
    else:
        team1_h2h_vs_rival = set(tie_teams[0][1]['h2h']) & set([tie_teams[1][0]])

        if len(team1_h2h_vs_rival) == 0:
            tie_teams = tie_teams[1:] + tie_teams[:1]

    return tie_teams

def three_way_tie(tie_teams: list) -> list:
    if len(tie_teams) != 3:
        print('not 3 way tie')
    else:        
        teams = [x[0] for x in tie_teams]
        for index, team  in enumerate(tie_teams): #one team superiority vs the other 2                   
            team_h2h = set(tie_teams[index][1]['h2h']) & set(teams)
    
            if len(team_h2h) == 2:                
                pop_team = tie_teams.pop(index)                                             
                remaining_tie = two_teams_tie(tie_teams)
                tie_teams = [pop_team] + remaining_tie
            
            elif index == 2:
                print('Round diff needed')
        
    return tie_teams

def tiebreaker(tie_teams):
    amount_tie_teams = len(tie_teams)
    if amount_tie_teams >= 4:
        match_tie_set = set()
        for team in tie_teams: #This need to be check
            match_tie_set.add(team[1]["matchDelta"])  
        if amount_tie_teams != match_tie_set:
            pass 
        
    if amount_tie_teams == 3:
        tie_teams = three_way_tie(tie_teams)
        
    if amount_tie_teams == 2:  # Esto se puede cambiar y modificar solo la posición
        
        tie_teams = two_teams_tie(tie_teams)
        
    return tie_teams or []

def untie(up_dict_sorted,dict_up_position):
    positon = 1
    return_dict = []
    for list_team in up_dict_sorted:
        if len(list_team) == 1:            
            dict_up_position[list_team[0][0]][str(positon)] += 1
            positon += 1
            return_dict += [list_team]
        if len(list_team) > 1:           
            sorted_dict_temp = tiebreaker(list_team)
            for team in sorted_dict_temp:             
                dict_up_position[team[0]][str(positon)] += 1
                positon += 1
            return_dict += sorted_dict_temp          
    return return_dict

In [18]:
dict_up_position = {}
for team in teamNameScores["name"]:
    dict_up_position[team] = {
        "1": 0,
        "2": 0,
        "3": 0,
        "4": 0,
        "5": 0,
        "6": 0,
        "7": 0,
        "8": 0,
        "9": 0,
        "10": 0,
        "11": 0,
        "12": 0,
    }

In [22]:
teams = teamNameScores
matches = (("Kru","Lev"), ("100T","mibr"),("NRG","EG"), ("FUR","LOUD"),("2G","G2"),("C9","SEN"))
matches2 = (["Kru","100T"], ["Lev","mibr"],["NRG","FUR"], ["EG","LOUD"],["C9","G2"],["2G","SEN"])

In [23]:
match1_results = run_round_delta(matches, teams)

In [12]:
len(match1_results)/12

4096.0

In [145]:
match2_results = run_round_delta(matches2,teams,match1_results[:1200])

In [35]:
(match1_results)

[{'UP': '1-1',
  'Team': 'Kru',
  'wins': 6,
  'matchDelta': 3,
  'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']},
 {'UP': '1-1',
  'Team': 'Lev',
  'wins': 10,
  'matchDelta': 17,
  'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']},
 {'UP': '1-1',
  'Team': '100T',
  'wins': 5,
  'matchDelta': -1,
  'h2h': ['EG', 'G2', 'NRG']},
 {'UP': '1-1',
  'Team': 'mibr',
  'wins': 2,
  'matchDelta': -13,
  'h2h': ['EG', '100T']},
 {'UP': '1-1',
  'Team': 'NRG',
  'wins': 4,
  'matchDelta': -5,
  'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']},
 {'UP': '1-1',
  'Team': 'EG',
  'wins': 5,
  'matchDelta': -3,
  'h2h': ['SEN', 'LOUD', 'NRG']},
 {'UP': '1-1',
  'Team': 'FUR',
  'wins': 3,
  'matchDelta': -9,
  'h2h': ['100T', 'mibr']},
 {'UP': '1-1',
  'Team': 'LOUD',
  'wins': 5,
  'matchDelta': -1,
  'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']},
 {'UP': '1-1',
  'Team': '2G',
  'wins': 7,
  'matchDelta': 5,
  'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']},
 {'UP': '1-1', 'Team':

In [26]:
groupby_up = groupby_UP(match1_results)

In [27]:
dict_ready_to_sort = heriarchy_dict_for_sort(groupby_up)

In [159]:
def sort_dict_by_wins(single_up_round):
    count = 1
    sorted_table = sorted(single_up_round.items(), key =lambda x: (x[1]["wins"], x[1]["matchDelta"]), reverse=True)
    
    grouped_table = group_table(sorted_table)
    
    count += 1
    return grouped_table
#Aca tengo que agregar el desempate y los resultados y no crear todo la lista larga? 

In [153]:
def two_teams_tie(tie_teams):
    if len(tie_teams) != 2:
        print("not 2 tie teams")
    else:
        team1_h2h_vs_rival = set(tie_teams[0][1]['h2h']) & set([tie_teams[1][0]])

        if len(team1_h2h_vs_rival) == 0:
            tie_teams = tie_teams[1:] + tie_teams[:1]

    return tie_teams

In [154]:
def three_way_tie(tie_teams):
    if len(tie_teams) != 3:
        print('not 3 way tie')
    else:
        
        teams = [x[0] for x in tie_teams]
        for index, team  in enumerate(tie_teams): #one team superiority vs the other 2                   
            team_h2h = set(tie_teams[index][1]['h2h']) & set(teams)
    
            if len(team_h2h) == 2:                
                pop_team = tie_teams.pop(index)                                             
                remaining_tie = two_teams_tie(tie_teams)
                tie_teams = [pop_team] + remaining_tie
            
            elif index == 2:
                print('Round diff needed')

        
    return tie_teams

In [155]:
def tiebreaker(tie_teams):
    amount_tie_teams = len(tie_teams)
    if amount_tie_teams >= 4:
        match_tie_set = set()
        for team in tie_teams: #This need to be check
            match_tie_set.add(team[1]["matchDelta"])  
        if amount_tie_teams != match_tie_set:
            pass 
        
    if amount_tie_teams == 3:
        tie_teams = three_way_tie(tie_teams)
        
    if amount_tie_teams == 2:  # Esto se puede cambiar y modificar solo la posición
        
        tie_teams = two_teams_tie(tie_teams)
        
    return tie_teams or []

In [156]:
def untie(up_dict_sorted,dict_up_position):
    positon = 1
    return_dict = []
    for list_team in up_dict_sorted:
        if len(list_team) == 1:            
            dict_up_position[list_team[0][0]][str(positon)] += 1
            positon += 1
            return_dict += [list_team]
        if len(list_team) > 1:           
            sorted_dict_temp = tiebreaker(list_team)
            for team in sorted_dict_temp:             
                dict_up_position[team[0]][str(positon)] += 1
                positon += 1
            return_dict += sorted_dict_temp          
    return return_dict

In [21]:
dict_up_h2h = {}
for team in teamNameScores["name"]:
    dict_up_h2h[team] = []

In [222]:
dict_up_h2h = {}
for team in teamNameScores["name"]:
    dict_up_h2h[team] = []

dict_up_h2h["Kru"].append("FUR")
dict_up_h2h["Kru"].append("mibr")
dict_up_h2h["Kru"].append("EG")
dict_up_h2h["Kru"].append("LOUD")
dict_up_h2h["Kru"].append("100T")
dict_up_h2h["Kru"].append("C9")
dict_up_h2h["Kru"].append("SEN")

dict_up_h2h["Lev"].append("SEN")
dict_up_h2h["Lev"].append("NRG")
dict_up_h2h["Lev"].append("G2")
dict_up_h2h["Lev"].append("Kru")
dict_up_h2h["Lev"].append("mibr")
dict_up_h2h["Lev"].append("100T")
dict_up_h2h["Lev"].append("EG")
dict_up_h2h["Lev"].append("LOUD")
dict_up_h2h["Lev"].append("FUR")

dict_up_h2h["2G"].append("FUR")
dict_up_h2h["2G"].append("EG")
dict_up_h2h["2G"].append("mibr")
dict_up_h2h["2G"].append("C9")
dict_up_h2h["2G"].append("Kru")
dict_up_h2h["2G"].append("C9")
dict_up_h2h["2G"].append("NRG")
dict_up_h2h["2G"].append("Kru")
dict_up_h2h["2G"].append("SEN")

dict_up_h2h["SEN"].append("100T")
dict_up_h2h["SEN"].append("mibr")
dict_up_h2h["SEN"].append("FUR")
dict_up_h2h["SEN"].append("NRG")
#dict_up_h2h["SEN"].append("Kru")
dict_up_h2h["SEN"].append("C9")

dict_up_h2h["C9"].append("Lev")
dict_up_h2h["C9"].append("EG")
dict_up_h2h["C9"].append("LOUD")
dict_up_h2h["C9"].append("FUR")
dict_up_h2h["C9"].append("mibr")
dict_up_h2h["C9"].append("NRG")

dict_up_h2h["100T"].append("G2")
dict_up_h2h["100T"].append("C9")
dict_up_h2h["100T"].append("NRG")
dict_up_h2h["100T"].append("mibr")
dict_up_h2h["100T"].append("EG")

dict_up_h2h["NRG"].append("LOUD")
dict_up_h2h["NRG"].append("FUR")
dict_up_h2h["NRG"].append("mibr")
dict_up_h2h["NRG"].append("Kru")

dict_up_h2h["LOUD"].append("SEN")
dict_up_h2h["LOUD"].append("G2")
dict_up_h2h["LOUD"].append("mibr")
dict_up_h2h["LOUD"].append("100T")

dict_up_h2h["EG"].append("SEN")
dict_up_h2h["EG"].append("NRG")
dict_up_h2h["EG"].append("LOUD")
dict_up_h2h["EG"].append("FUR")

dict_up_h2h["FUR"].append("100T")
dict_up_h2h["FUR"].append("LOUD")
dict_up_h2h["FUR"].append("mibr")

dict_up_h2h["mibr"].append("EG")



In [29]:
dict_ready_to_sort

{'1-1': {'Kru': {'wins': 6,
   'matchDelta': 3,
   'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']},
  'Lev': {'wins': 10,
   'matchDelta': 17,
   'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']},
  '100T': {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']},
  'mibr': {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']},
  'NRG': {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']},
  'EG': {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']},
  'FUR': {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']},
  'LOUD': {'wins': 5,
   'matchDelta': -1,
   'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']},
  '2G': {'wins': 7,
   'matchDelta': 5,
   'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']},
  'G2': {'wins': 1, 'matchDelta': 2, 'h2h': ['2G']},
  'C9': {'wins': 6,
   'matchDelta': -2,
   'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG']},
  'SEN': {'wins': 7,
   'matchDelta': 7,
   'h2h': ['100T', 'mibr', 'FUR', 'NRG', 'C9']}},
 '

In [30]:
test_sort = sort_dict_by_wins(dict_ready_to_sort["1-3"])

In [33]:
test_sort

[[('Lev',
   {'wins': 10,
    'matchDelta': 17,
    'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']})],
 [('2G',
   {'wins': 7,
    'matchDelta': 5,
    'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']}),
  ('C9',
   {'wins': 7,
    'matchDelta': 1,
    'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG', 'SEN']})],
 [('SEN', {'wins': 6, 'matchDelta': 4, 'h2h': ['100T', 'mibr', 'FUR', 'NRG']}),
  ('Kru',
   {'wins': 6,
    'matchDelta': 3,
    'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']})],
 [('100T', {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']}),
  ('LOUD',
   {'wins': 5, 'matchDelta': -1, 'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']}),
  ('EG', {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']})],
 [('NRG',
   {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']})],
 [('FUR', {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']})],
 [('mibr', {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']})],
 [('G2', {'wins': 1,

In [31]:
test_sort_2 = untie(test_sort,dict_up_position)

Round diff needed


In [32]:
test_sort_2

[[('Lev',
   {'wins': 10,
    'matchDelta': 17,
    'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']})],
 ('C9',
  {'wins': 7,
   'matchDelta': 1,
   'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG', 'SEN']}),
 ('2G',
  {'wins': 7,
   'matchDelta': 5,
   'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']}),
 ('Kru',
  {'wins': 6,
   'matchDelta': 3,
   'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']}),
 ('SEN', {'wins': 6, 'matchDelta': 4, 'h2h': ['100T', 'mibr', 'FUR', 'NRG']}),
 ('100T', {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']}),
 ('LOUD',
  {'wins': 5, 'matchDelta': -1, 'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']}),
 ('EG', {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']}),
 [('NRG',
   {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']})],
 [('FUR', {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']})],
 [('mibr', {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']})],
 [('G2', {'wins': 1, 'matchDelta': 2, 'h

In [250]:
import copy

tie_teams_copy = copy.deepcopy(test_sort)

tie_teams = untie(tie_teams_copy,dict_up_h2h,dict_up_position)

entro if len
Updated tie_teams: [('C9', {'wins': 7, 'matchDelta': 1, 'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG', 'SEN']}), ('2G', {'wins': 7, 'matchDelta': 5, 'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']})]
entro if len
Updated tie_teams: [('Kru', {'wins': 6, 'matchDelta': 3, 'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']}), ('SEN', {'wins': 6, 'matchDelta': 4, 'h2h': ['100T', 'mibr', 'FUR', 'NRG']})]


In [252]:
tie_teams_copy

[[('Lev',
   {'wins': 10,
    'matchDelta': 17,
    'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']})],
 [('2G',
   {'wins': 7,
    'matchDelta': 5,
    'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']}),
  ('C9',
   {'wins': 7,
    'matchDelta': 1,
    'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG', 'SEN']})],
 [('SEN', {'wins': 6, 'matchDelta': 4, 'h2h': ['100T', 'mibr', 'FUR', 'NRG']}),
  ('Kru',
   {'wins': 6,
    'matchDelta': 3,
    'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']})],
 [('100T', {'wins': 5, 'matchDelta': -1, 'h2h': ['EG', 'G2', 'NRG']}),
  ('LOUD',
   {'wins': 5, 'matchDelta': -1, 'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR']}),
  ('EG', {'wins': 5, 'matchDelta': -3, 'h2h': ['SEN', 'LOUD', 'NRG']})],
 [('NRG',
   {'wins': 4, 'matchDelta': -5, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']})],
 [('FUR', {'wins': 3, 'matchDelta': -9, 'h2h': ['100T', 'mibr']})],
 [('mibr', {'wins': 2, 'matchDelta': -13, 'h2h': ['EG', '100T']})],
 [('G2', {'wins': 1,

In [160]:
for key in dict_ready_to_sort.keys():
    sorted_table = sort_dict_by_wins(dict_ready_to_sort[key])
    untie(sorted_table,dict_up_position) 

Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff

In [140]:
dict_up_position

{'Kru': {'1': 0,
  '2': 512,
  '3': 1536,
  '4': 1920,
  '5': 128,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'Lev': {'1': 4096,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 '100T': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 640,
  '6': 3456,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'mibr': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 4096,
  '12': 0},
 'NRG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1920,
  '8': 1152,
  '9': 1024,
  '10': 0,
  '11': 0,
  '12': 0},
 'EG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1536,
  '8': 512,
  '9': 1280,
  '10': 768,
  '11': 0,
  '12': 0},
 'FUR': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 512,
  '9': 1280,
  '10': 2304,
  '11': 0,
  '12': 0},
 'LOUD': {'1': 0,
  '2': 0,
  '3':

In [122]:
untie(test_sort, dict_up_h2h, dict_up_position)

entro
entro
entro en 3


In [124]:
dict_up_position

{'Kru': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 1,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'Lev': {'1': 1,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 '100T': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 1,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'mibr': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 1,
  '12': 0},
 'NRG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 1,
  '10': 0,
  '11': 0,
  '12': 0},
 'EG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 1,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'FUR': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 1,
  '11': 0,
  '12': 0},
 'LOUD': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1,
  '8

In [120]:
dict_up_position

{'Kru': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 1,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'Lev': {'1': 1,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 '100T': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 1,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'mibr': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 0,
  '11': 1,
  '12': 0},
 'NRG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 1,
  '10': 0,
  '11': 0,
  '12': 0},
 'EG': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 1,
  '9': 0,
  '10': 0,
  '11': 0,
  '12': 0},
 'FUR': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 0,
  '8': 0,
  '9': 0,
  '10': 1,
  '11': 0,
  '12': 0},
 'LOUD': {'1': 0,
  '2': 0,
  '3': 0,
  '4': 0,
  '5': 0,
  '6': 0,
  '7': 1,
  '8

In [124]:
sorted_values = sorted_list_of_up_dict(dict_ready_to_sort)

In [122]:
sorted_result = []

for key in dict_ready_to_sort.keys():
    single_up_sorted = sort_dict_by_wins(dict_ready_to_sort[key])
    sorted_result.append(single_up_sorted)
    

In [121]:
sorted_result

[[[('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('SEN', {'wins': 1, 'matchWins': 2, 'matchLoss': 0})],
  [('Kru', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('100T', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('NRG', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('FUR', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('2G', {'wins': 0, 'matchWins': 0, 'matchLoss': 2}),
   ('C9', {'wins': 0, 'matchWins': 0, 'matchLoss': 2})]],
 [[('Lev', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('mibr', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('EG', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('LOUD', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('GAMERS2', {'wins': 1, 'matchWins': 2, 'matchLoss': 0}),
   ('SEN', {'wins':

In [98]:
round1_df = pd.DataFrame(match1_results)

In [101]:
test_woking = round1_df

In [11]:
match2_results = run_round(matches, teams, match1_results)